In [1]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from gensim.models import FastText
import re
import string
import nltk
import joblib
import pickle
from bs4 import BeautifulSoup
import gensim 
from gensim.models import Word2Vec 
from nltk.corpus import stopwords
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [2]:
data = pd.read_csv("final_data.csv")
y = data.target
X = data.drop(["target"],axis=1)

### Split data into training and testing

In [3]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=1)

In [4]:
string_cols = np.load("string_cols.npy")
numerical_cols = np.load("numerical_cols.npy")
boolean_cols = np.load("boolean_cols.npy")

In [5]:
numerical_cols = [col for col in numerical_cols if col!="target"]
string_cols = [col for col in string_cols if col in X_train.columns]

In [6]:
print(numerical_cols)
print(X_train.columns)

['created', 'created_utc', 'gilded', 'num_comments', 'num_crossposts', 'num_duplicates', 'score', 'subreddit_subscribers', 'thumbnail_height', 'thumbnail_width', 'total_awards_received', 'ups', 'upvote_ratio', 'wls']
Index(['Unnamed: 0', 'allow_live_comments', 'archived', 'author',
       'author_flair_background_color', 'author_flair_css_class',
       'author_flair_template_id', 'author_flair_text',
       'author_flair_text_color', 'author_flair_type', 'author_fullname',
       'author_premium', 'comments', 'contest_mode', 'created', 'created_utc',
       'domain', 'gilded', 'hide_score', 'id', 'is_original_content',
       'is_reddit_media_domain', 'is_self', 'is_video',
       'link_flair_background_color', 'link_flair_css_class',
       'link_flair_template_id', 'link_flair_text_color', 'link_flair_type',
       'locked', 'name', 'no_follow', 'num_comments', 'num_crossposts',
       'num_duplicates', 'permalink', 'post_hint', 'score', 'selftext',
       'selftext_html', 'send_rep

## Handle Numerical Features

### Scale the numerical features & Remove columns with 0 stddev

In [7]:
scaler = MinMaxScaler()

numeric_X_train = X_train[numerical_cols]
numeric_X_test = X_test[numerical_cols]
numeric_X_train_minmax = scaler.fit_transform(numeric_X_train)
numeric_X_train_minmax = pd.DataFrame(numeric_X_train_minmax, index=numeric_X_train.index, columns=numeric_X_train.columns)
numeric_X_train_minmax = numeric_X_train_minmax.loc[:, numeric_X_train_minmax.std() > 0]
final_numeric_cols = numeric_X_train_minmax.columns
joblib.dump(scaler, 'scaler.pkl')

['scaler.pkl']

In [8]:
numerical_cols = final_numeric_cols

### Transform numerical columns of testing data

In [9]:
numeric_X_test_minmax = scaler.transform(numeric_X_test)
numeric_X_test_minmax = pd.DataFrame(numeric_X_test_minmax, index=numeric_X_test.index, columns=numeric_X_test.columns)
numeric_X_test_minmax = numeric_X_test_minmax[final_numeric_cols]

X_train = X_train.drop(numerical_cols,axis=1)
X_test = X_test.drop(numerical_cols,axis=1)
X_test_final___ = X_test.join(numeric_X_test_minmax)
X_train_final___ = X_train.join(numeric_X_train_minmax)

In [10]:
X_train = X_train_final___
X_test = X_test_final___

## Handle Textual Features

### Collect all textual data

In [11]:
all_texts = []
for col in string_cols:
    for row in X_train.iterrows():
        all_texts.append(row[1][col])

### Tokenize the textual data

In [12]:
all_tokens = []
stop_words = set(stopwords.words('english'))       
for sentence in all_texts:
    try:
        tokens_ = nltk.word_tokenize(sentence)
    except:
        tokens_ = nltk.word_tokenize("")
    final_tokens = [w for w in tokens_ if not w in stop_words] 
    all_tokens.append(final_tokens)
all_tokens = np.array(all_tokens)

### Create a Vector Representative Model using all tokens

In [13]:
fastText_model = FastText(all_tokens, min_count=1,size=10)
word2ec = gensim.models.Word2Vec(all_tokens, min_count = 1, size = 10, window = 5)

In [14]:
import joblib 
joblib.dump(fastText_model, 'fastText.pkl')
joblib.dump(word2ec, 'word2ec.pkl')

['fastText.pkl']

['word2ec.pkl']

In [15]:
def buildWordVector(sentence,model):
    print(model)
    try:
        tokens_ = nltk.word_tokenize(sentence)
    except:
        tokens_ = nltk.word_tokenize("")
    tokens = [w for w in tokens_ if not w in stop_words]  
    size=10
    vec = np.zeros(size).reshape((1, size))
    count = 0.
    for word in tokens:
        try:
            vec += model.wv[word].reshape((1, size))
        except:
            vec += np.zeros(size).reshape((1, size))
        count += 1.
    if count != 0:
        vec /= count
    return vec

In [16]:
def convert_strings_to_vectors(col,df,model):
    temp = [buildWordVector(x,model) for x in df[col]]
    temp_ = [list(np.ravel(x)) for x in temp]
    temp_df = pd.DataFrame([temp_])
    temp_df_t = temp_df.transpose()
    temp_df_t.columns = [col]
    temp_df_t.index = df.index
    df = df.drop(columns = [col])
    df = df.join(temp_df_t)
    return df

### Convert string columns to vectors using FastText

In [17]:
X_train_fastText = X_train.copy()
X_test_fastText = X_test.copy()

In [18]:
string_col = string_cols.copy()
for col in string_cols:
    X_train_fastText = convert_strings_to_vectors(col,X_train_fastText,fastText_model)
    X_test_fastText = convert_strings_to_vectors(col,X_test_fastText,fastText_model)

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

...

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, alpha=0.025)
FastText(vocab=50368, size=10, a

In [19]:
X_train_fastText.to_csv("training_data.csv",header=True)
X_test_fastText.to_csv("testing_data.csv",header=True)
y_train.to_csv("training_labels.csv",header=True)
y_test.to_csv("testing_labels.csv",header=True)

### Convert string columns to vectors using Word2Vec

In [20]:
X_train_word2vec = X_train.copy()
X_test_word2vec = X_test.copy()

In [21]:
string_col = string_cols.copy()
for col in string_cols:
    X_train_word2vec = convert_strings_to_vectors(col,X_train_word2vec,word2ec)
    X_test_word2vec = convert_strings_to_vectors(col,X_test_word2vec,word2ec)

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

...

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, alpha=0.025)
Word2Vec(vocab=50368, size=10, a

In [22]:
X_train_word2vec.to_csv("training_data2.csv",header=True)
X_test_word2vec.to_csv("testing_data2.csv",header=True)
y_train.to_csv("training_labels2.csv",header=True)
y_test.to_csv("testing_labels2.csv",header=True)

In [23]:
X_train_fastText

Unnamed: 0  allow_live_comments  archived  author_premium  contest_mode  \
0              0                    0         0               0             0   
816          816                    0         0               1             0   
790          790                    0         1               0             0   
361          361                    0         1               0             0   
592          592                    0         1               1             0   
1675        1675                    0         0               0             0   
115          115                    0         1               0             0   
1079        1079                    0         0               1             0   
546          546                    0         1               0             0   
336          336                    0         1               0             0   
1225        1225                    0         1               0             0   
1656        1656                    0         0               0             0   
201          201                    0         0               0             0   
906          906                    1         0               0             0   
30            30                    0         1               0             0   
424          424                    0         1               0             0   
1583        1583                    0         1               0             0   
1631        1631                    1         0               0             0   
1153        1153                    0         1               0             0   
1781        1781                    0         1               0             0   
1754        1754                    1         1               0             0   
608          608                    0         0               1             0   
1671        1671                    0         1               0             0   
969          969                    0         0               0             0   
293          293                    0         1               0             0   
305          305                    0         1               0             0   
653          653                    0         0               0             0   
1463        1463                    0         1               0             0   
146          146                    0         1               0             0   
968          968                    0         0               0             0   
...          ...                  ...       ...             ...           ...   
562          562                    0         0               1             0   
398          398                    0         1               0             0   
1949        1949                    0         0               0             0   
668          668                    0         1               0             0   
1514        1514                    0         1               0             0   
252          252                    0         1               0             0   
907          907                    1         0               0             0   
468          468                    0         1               0             0   
914          914                    0         0               0             0   
357          357                    0         1               0             0   
1278        1278                    0         1               0             0   
1300        1300                    0         1               0             0   
1202        1202                    1         1               0             0   
1305        1305                    0         1               0             0   
1414        1414                    0         1               0             0   
508          508                    0         0               0             0   
749          749                    0         1               0             0   
1607        1607                    0

In [24]:
X_train_word2vec

Unnamed: 0  allow_live_comments  archived  author_premium  contest_mode  \
0              0                    0         0               0             0   
816          816                    0         0               1             0   
790          790                    0         1               0             0   
361          361                    0         1               0             0   
592          592                    0         1               1             0   
1675        1675                    0         0               0             0   
115          115                    0         1               0             0   
1079        1079                    0         0               1             0   
546          546                    0         1               0             0   
336          336                    0         1               0             0   
1225        1225                    0         1               0             0   
1656        1656                    0         0               0             0   
201          201                    0         0               0             0   
906          906                    1         0               0             0   
30            30                    0         1               0             0   
424          424                    0         1               0             0   
1583        1583                    0         1               0             0   
1631        1631                    1         0               0             0   
1153        1153                    0         1               0             0   
1781        1781                    0         1               0             0   
1754        1754                    1         1               0             0   
608          608                    0         0               1             0   
1671        1671                    0         1               0             0   
969          969                    0         0               0             0   
293          293                    0         1               0             0   
305          305                    0         1               0             0   
653          653                    0         0               0             0   
1463        1463                    0         1               0             0   
146          146                    0         1               0             0   
968          968                    0         0               0             0   
...          ...                  ...       ...             ...           ...   
562          562                    0         0               1             0   
398          398                    0         1               0             0   
1949        1949                    0         0               0             0   
668          668                    0         1               0             0   
1514        1514                    0         1               0             0   
252          252                    0         1               0             0   
907          907                    1         0               0             0   
468          468                    0         1               0             0   
914          914                    0         0               0             0   
357          357                    0         1               0             0   
1278        1278                    0         1               0             0   
1300        1300                    0         1               0             0   
1202        1202                    1         1               0             0   
1305        1305                    0         1               0             0   
1414        1414                    0         1               0             0   
508          508                    0         0               0             0   
749          749                    0         1               0             0   
1607        1607                    0